# time is 23:10: I know you can do that. NEVER KEBAB

In [ ]:
# Install required libraries
!pip install nltk spacy text2emotion
!python -m spacy download en_core_web_sm


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 142.5 MB/s eta 0:00:00
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')
⚠ Restart to reload dependencies
If you are in a Jupyter or Colab notebook, you may need to restart Python in
order to load all the package's dependencies. You can do this by selecting the
'Restart kernel' or 'Restart runtime' option.


In [ ]:
# importing necessary libs

# leave it here for now (will update later)
import pickle
import numpy as np
import re
import nltk
import spacy

In [ ]:
# Download necessary NLTK packages if you don't have them
nltk.download('punkt')

# Load the spaCy model for tokenization
nlp = spacy.load("en_core_web_sm")


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [ ]:
def load_pickle(file_path):
    with open(file_path, 'rb') as f:
        return pickle.load(f, encoding='latin1') # encoding important since python 2 version were used

train_annotations = load_pickle('/content/annotation_training.pkl')
valid_annotations = load_pickle('/content/annotation_validation.pkl')
test_annotations = load_pickle('/content/annotation_test.pkl')

train_transcriptions = load_pickle('/content/transcription_training.pkl')
valid_transcriptions = load_pickle('/content/transcription_validation.pkl')
test_transcriptions = load_pickle('/content/transcription_test.pkl')

# Verify the structure of loaded data (annotations and transcriptions)
print("Train annotations:", list(train_annotations.items())[:1])
print("Train transcriptions:", list(train_transcriptions.items())[:1])


Train annotations: [('extraversion', {'J4GQm9j0JZ0.003.mp4': 0.5233644859813085, 'zEyRyTnIw5I.005.mp4': 0.3457943925233645, 'nskJh7v6v1U.004.mp4': 0.25233644859813087, '6wHQsN5g2RM.000.mp4': 0.4579439252336449, 'dQOeQYWIgm8.000.mp4': 0.6074766355140188, 'eHcRre1YsNA.000.mp4': 0.19626168224299068, 'vZpneJlniAE.005.mp4': 0.4205607476635514, 'oANKg9_grdA.004.mp4': 0.4299065420560748, 'VuadgOz6T7s.000.mp4': 0.22429906542056074, '7nhJXn9PI0I.001.mp4': 0.17757009345794392, 'tEQEKN07KgQ.001.mp4': 0.20560747663551404, 'I5x9T9ftW18.005.mp4': 0.663551401869159, 'dh6iOU2RtTA.003.mp4': 0.6074766355140188, 'gsleSGEZHAs.004.mp4': 0.37383177570093457, 'vhugKRUnd-c.001.mp4': 0.4112149532710281, 'kn6I8LdQFN0.004.mp4': 0.18691588785046728, 'M5_x5J-H2I0.003.mp4': 0.4672897196261683, 'w_ExyXsnw2A.000.mp4': 0.4299065420560748, 'DnTtbAR_Qyw.004.mp4': 0.6542056074766356, 'rIHcq2E67Nc.005.mp4': 0.6355140186915887, 'De4i7-FX9Og.004.mp4': 0.663551401869159, 'cA43Gfcg0QA.000.mp4': 0.1588785046728972, 'pZxqWp0e-I

# high-level preprocessing

In [ ]:
def preprocess_high_level(data):
    """
    High-level preprocessing to filter out short transcriptions based on length.
    We calculate the transcription length for each video and remove those below the threshold.
    """
    # Calculate the length of each transcription
    lengths = [len(content['transcription'].split()) for content in data.values()]

    # Calculate mean and standard deviation
    mean_len = np.mean(lengths)
    std_len = np.std(lengths)

    # Define a threshold: keep only those with length > mean - 2 * std
    threshold = mean_len - 2 * std_len

    # Filter out short transcriptions
    filtered_data = {
        video_id: content for video_id, content in data.items()
        if len(content['transcription'].split()) > threshold
    }

    return filtered_data


# low-level preprocessing

In [ ]:
# Normalize text: Convert to lowercase, remove URLs, emails, punctuation, and extra spaces
def normalize_text(text):
    """
    Normalize text by:
    - Lowercasing
    - Removing URLs, emails, punctuation
    - Replacing repeated characters (e.g., "hooooray" -> "hooray")
    - Removing extra spaces
    """
    # Convert text to lowercase
    text = text.lower()

    # Remove URLs and emails
    text = re.sub(r'http\S+|www\S+', '', text)
    text = re.sub(r'\S+@\S+', '', text)

    # Remove punctuation
    text = re.sub(r'[^\w\s]', '', text)

    # Replace repeated characters (e.g., "hooooray" -> "hooray")
    text = re.sub(r'(.)\1+', r'\1\1', text)

    # Remove extra spaces
    text = re.sub(r'\s+', ' ', text).strip()

    return text

# Fix spaces in words (e.g., 'manif estation' -> 'manifestation')
def fix_spaces(text):
    """
    Fix misplaced spaces in words (e.g., 'manif estation' -> 'manifestation').
    This uses a simple dictionary-based approach.
    """
    words = text.split()
    corrected_words = []

    # Use a dictionary for space inference (simple version for illustration)
    dictionary = set(nlp.vocab.strings)

    for word in words:
        if word not in dictionary:
            # Heuristic to split words (a better version could use a larger dictionary)
            for i in range(1, len(word)):
                if word[:i] in dictionary and word[i:] in dictionary:
                    corrected_words.append(word[:i])
                    corrected_words.append(word[i:])
                    break
            else:
                corrected_words.append(word)  # If no split, keep original
        else:
            corrected_words.append(word)

    return ' '.join(corrected_words)

# Low-level preprocessing: Apply normalization and space fixing
def preprocess_low_level(data):
    """
    Low-level preprocessing to clean and normalize the transcriptions.
    - Normalize the text (lowercase, remove unwanted characters).
    - Fix space issues in words.
    """
    processed_data = {}
    for video_id, content in data.items():
        # Normalize and fix spaces in transcription
        transcription = content['transcription']
        normalized_transcription = normalize_text(transcription)
        fixed_transcription = fix_spaces(normalized_transcription)

        processed_data[video_id] = {
            "transcription": fixed_transcription,
            "annotations": content["annotations"]
        }
    return processed_data

# But first we need to combine those given pickles, instead of working with 6 files

In [ ]:
# Correct function to combine annotations and transcriptions
def combine_annotations_and_transcriptions(annotations, transcriptions):
    combined_data = {}

    # Iterate over each annotation in the annotations list
    for trait, annotation_dict in annotations.items():
        # For each trait's annotation, map the video IDs to the scores
        for video_id, score in annotation_dict.items():
            if video_id in transcriptions:
                # If the video_id exists in transcriptions, combine it
                if video_id not in combined_data:
                    combined_data[video_id] = {"transcription": transcriptions[video_id]}

                # Add the trait score to the combined data for the video_id
                combined_data[video_id].setdefault("annotations", {})[trait] = float(score)

    return combined_data

In [ ]:
# Combine data for train, validation, and test
train_combined_data = combine_annotations_and_transcriptions(train_annotations, train_transcriptions)
valid_combined_data = combine_annotations_and_transcriptions(valid_annotations, valid_transcriptions)
test_combined_data = combine_annotations_and_transcriptions(test_annotations, test_transcriptions)

# print(train_transcriptions)
print(train_combined_data)

# Perform high-level preprocessing
train_combined_data = preprocess_high_level(train_combined_data)
print("high level preprocessing for train is DONE")
valid_combined_data = preprocess_high_level(valid_combined_data)
print("high level preprocessing for val is DONE")
test_combined_data = preprocess_high_level(test_combined_data)
print("high level preprocessing for test is DONE")

# Perform low-level preprocessing
train_combined_data = preprocess_low_level(train_combined_data)
print("low level preprocessing for train is DONE")
valid_combined_data = preprocess_low_level(valid_combined_data)
print("low level preprocessing for val is DONE")
test_combined_data = preprocess_low_level(test_combined_data)
print("low level preprocessing for test is DONE")

# Display an example of preprocessed data
print(f"Processed example from train data: {list(train_combined_data.items())}")


{'J4GQm9j0JZ0.003.mp4': {'transcription': 'He\'s cutting it and then turn around and see the end result, but I\'m glad he didn\'t do that because I probably would\'ve lost my mind. As it was getting cut, I was just excited. I saw the snippets of hair falling to the floor and I was like, "Yes!"', 'annotations': {'extraversion': 0.5233644859813085, 'neuroticism': 0.5520833333333334, 'agreeableness': 0.6263736263736264, 'conscientiousness': 0.6019417475728155, 'interview': 0.5046728971962616, 'openness': 0.4888888888888889}}, 'zEyRyTnIw5I.005.mp4': {'transcription': 'Responsibility to house the organ I had been given and I needed to tell them I was going to take good care of that organ and that I so appreciated what they had done. Almost immediately I sent a letter to them', 'annotations': {'extraversion': 0.3457943925233645, 'neuroticism': 0.37499999999999994, 'agreeableness': 0.4725274725274725, 'conscientiousness': 0.5825242718446602, 'interview': 0.4579439252336448, 'openness': 0.3666

# Wav2Vec

In [ ]:
!pip install gensim

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 27.9/27.9 MB 94.7 MB/s eta 0:00:00


In [ ]:
from gensim.models import Word2Vec

# Fast tokenizer
def tokenize_text(text):
    return text.split()

train_tokens = [tokenize_text(content['transcription']) for content in train_combined_data.values()]
valid_tokens = [tokenize_text(content['transcription']) for content in valid_combined_data.values()]
test_tokens  = [tokenize_text(content['transcription']) for content in test_combined_data.values()]

# Train Word2Vec
word2vec_model = Word2Vec(
    sentences=train_tokens,
    vector_size=300,
    window=5,
    min_count=1,
    workers=4,
    sg=1,              # Skip-gram (good for semantic tasks)
    epochs=20          # You can raise to 50–100 for final training
)

word2vec_model.save("word2vec.model")

# Example usage
word = 'excited'
if word in word2vec_model.wv:
    print(word2vec_model.wv[word])
else:
    print(f"'{word}' not in vocabulary")

[-3.12010407e-01  5.29044628e-01 -2.20298812e-01 -7.86666945e-03
  9.68565717e-02 -2.24501252e-01  2.69446760e-01  4.56398278e-01
  4.06951368e-01  7.66932145e-02  9.04587135e-02 -2.63961069e-02
  1.38549507e-01  2.46126920e-01 -2.32047755e-02  9.04821083e-02
 -2.58468557e-02  4.01038304e-02 -1.80145919e-01 -1.95501804e-01
 -1.17831461e-01  2.00337738e-01  6.33048341e-02  3.17815274e-01
 -4.25315201e-01  2.28099555e-01 -2.21435264e-01  1.15100399e-01
 -6.97917119e-02 -1.29762381e-01  3.90046626e-01 -2.74263564e-02
 -4.09548506e-02  1.99085504e-01  1.16125576e-01  1.41212016e-01
  5.16856849e-01 -6.52623549e-02 -1.46072850e-01  6.25680387e-02
 -7.34046921e-02 -1.30488463e-02  9.52445120e-02 -6.66784197e-02
  4.87374395e-01  6.11523278e-02 -3.25880468e-01  4.57717478e-01
  2.42803007e-01  5.04750572e-02  5.25512770e-02  1.20770611e-01
  8.01744983e-02 -2.74701208e-01  5.23087800e-01  1.55612722e-01
  2.60665566e-01  1.40495747e-01  2.30589490e-02 -1.77611038e-01
 -2.40026444e-01 -1.47739

In [ ]:

# Assuming you still have train_annotations / valid_annotations / test_annotations loaded
# and train_combined_data / valid_combined_data / test_combined_data built earlier.

all_traits = [trait for trait, _ in train_annotations.items()]  # e.g. ['extraversion', 'agreeableness', ..., 'interview']
big5_traits = [t for t in all_traits if t.lower() != "interview"]
print("Big Five traits:", big5_traits)

# Fix a stable order of video IDs (so X and y align)
train_keys = list(train_combined_data.keys())
valid_keys = list(valid_combined_data.keys())
test_keys  = list(test_combined_data.keys())

def build_label_matrix(combined_data, keys, traits):
    y = []
    for vid in keys:
        ann = combined_data[vid]["annotations"]
        y.append([ann[t] for t in traits])
    return np.array(y, dtype=np.float32)

y_train = build_label_matrix(train_combined_data, train_keys, big5_traits)
y_valid = build_label_matrix(valid_combined_data, valid_keys, big5_traits)
y_test  = build_label_matrix(test_combined_data,  test_keys,  big5_traits)

print("y_train shape:", y_train.shape)  # (N_train, 5)


Big Five traits: ['extraversion', 'neuroticism', 'agreeableness', 'conscientiousness', 'openness']
y_train shape: (5764, 5)


In [ ]:
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

MAX_VOCAB_SIZE = 20000   # cap on vocab size
MAX_SEQ_LEN    = 84      # as in the paper after high-level filtering

# Collect texts in the same key order
train_texts = [train_combined_data[k]["transcription"] for k in train_keys]
valid_texts = [valid_combined_data[k]["transcription"] for k in valid_keys]
test_texts  = [test_combined_data[k]["transcription"]  for k in test_keys]

tokenizer = Tokenizer(num_words=MAX_VOCAB_SIZE, oov_token="<UNK>")
tokenizer.fit_on_texts(train_texts)

def texts_to_padded(texts):
    seqs = tokenizer.texts_to_sequences(texts)
    return pad_sequences(seqs, maxlen=MAX_SEQ_LEN, padding="post", truncating="post")

X_train = texts_to_padded(train_texts)
X_valid = texts_to_padded(valid_texts)
X_test  = texts_to_padded(test_texts)

vocab_size = min(MAX_VOCAB_SIZE, len(tokenizer.word_index) + 1)
print("X_train shape:", X_train.shape)
print("Vocab size:", vocab_size)


X_train shape: (5764, 84)
Vocab size: 10819


In [ ]:
EMB_DIM = 300  # must match the vector_size used in Word2Vec

embedding_matrix = np.zeros((vocab_size, EMB_DIM), dtype=np.float32)

for word, idx in tokenizer.word_index.items():
    if idx >= vocab_size:
        continue
    if word in word2vec_model.wv:
        embedding_matrix[idx] = word2vec_model.wv[word]
    # else: keep zero vector

print("Embedding matrix shape:", embedding_matrix.shape)


Embedding matrix shape: (10819, 300)


In [ ]:
import tensorflow as tf
from tensorflow.keras import layers, models

# Custom attention layer
class Attention(layers.Layer):
    def __init__(self, **kwargs):
        super().__init__(**kwargs)

    def build(self, input_shape):
        # input_shape = (batch, time, features)
        d = input_shape[-1]
        self.W = self.add_weight(
            name="W_att",
            shape=(d, d),
            initializer="glorot_uniform",
            trainable=True,
        )
        self.v = self.add_weight(
            name="v_att",
            shape=(d, 1),
            initializer="glorot_uniform",
            trainable=True,
        )
        super().build(input_shape)

    def call(self, inputs):
        # inputs: (batch, time, features)
        # score = v^T tanh(W h_t)
        score = tf.tensordot(inputs, self.W, axes=1)           # (batch, time, d)
        score = tf.nn.tanh(score)
        score = tf.tensordot(score, self.v, axes=1)            # (batch, time, 1)
        attention_weights = tf.nn.softmax(score, axis=1)       # (batch, time, 1)
        context = tf.reduce_sum(attention_weights * inputs, axis=1)  # (batch, d)
        return context

# Build model
inputs = layers.Input(shape=(MAX_SEQ_LEN,), name="input_ids")

embedding_layer = layers.Embedding(
    input_dim=vocab_size,
    output_dim=EMB_DIM,
    weights=[embedding_matrix],
    input_length=MAX_SEQ_LEN,
    trainable=True,      # you can set False first, then unfreeze for fine-tuning
    name="embedding",
)

x = embedding_layer(inputs)
x = layers.Bidirectional(layers.LSTM(128, return_sequences=True), name="bilstm")(x)
x = Attention(name="attention")(x)
x = layers.Dense(128, activation="relu", name="fc1")(x)
x = layers.Dropout(0.5)(x)
x = layers.Dense(64, activation="relu", name="fc2")(x)
outputs = layers.Dense(len(big5_traits), activation="linear", name="big5_outputs")(x)

model = models.Model(inputs=inputs, outputs=outputs)
model.summary()


/usr/local/lib/python3.12/dist-packages/keras/src/layers/core/embedding.py:97: UserWarning: Argument `input_length` is deprecated. Just remove it.
  warnings.warn(


Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ input_ids (InputLayer)          │ (None, 84)             │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ embedding (Embedding)           │ (None, 84, 300)        │     3,245,700 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ bilstm (Bidirectional)          │ (None, 84, 256)        │       439,296 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ attention (Attention)           │ (None, 256)            │        65,792 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ fc1 (Dense)                     │ (None, 128)            │        32,896 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ dropout (Dropout)               │ (None, 128)            │             0 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ fc2 (Dense)                     │ (None, 64)             │         8,256 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ big5_outputs (Dense)            │ (None, 5)              │           325 │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 3,792,265 (14.47 MB)

 Trainable params: 3,792,265 (14.47 MB)

 Non-trainable params: 0 (0.00 B)

In [ ]:
lr = 6e-4  # as mentioned in the paper
optimizer = tf.keras.optimizers.Adam(learning_rate=lr)

model.compile(
    optimizer=optimizer,
    loss="mae",
    metrics=["mae"],
)

BATCH_SIZE = 64
EPOCHS = 30  # you can go to 32+ as in the paper

history = model.fit(
    X_train, y_train,
    validation_data=(X_valid, y_valid),
    epochs=EPOCHS,
    batch_size=BATCH_SIZE,
)


Epoch 1/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 8s 27ms/step - loss: 0.2089 - mae: 0.2089 - val_loss: 0.1238 - val_mae: 0.1238
Epoch 2/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 7s 25ms/step - loss: 0.1327 - mae: 0.1327 - val_loss: 0.1145 - val_mae: 0.1145
Epoch 3/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.1242 - mae: 0.1242 - val_loss: 0.1132 - val_mae: 0.1132
Epoch 4/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.1187 - mae: 0.1187 - val_loss: 0.1137 - val_mae: 0.1137
Epoch 5/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.1121 - mae: 0.1121 - val_loss: 0.1217 - val_mae: 0.1217
Epoch 6/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.1070 - mae: 0.1070 - val_loss: 0.1203 - val_mae: 0.1203
Epoch 7/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 23ms/step - loss: 0.0993 - mae: 0.0993 - val_loss: 0.1156 - val_mae: 0.1156
Epoch 8/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 24ms/step - loss: 0.0929 - mae: 0.0929 - val_loss: 0.1174 - val_mae: 0.1174
Epoch 9/30
91/91 ━━━━━━━━━━━━━━━━━━━━ 2s 21ms/step - loss: 0.088

In [ ]:
test_loss, test_mae = model.evaluate(X_test, y_test, verbose=0)
print("Test MAE (overall):", test_mae)
print("Approx. accuracy (1 - MAE):", 1.0 - test_mae)

# Per-trait MAE and accuracy
y_pred = model.predict(X_test)

trait_mae = np.mean(np.abs(y_pred - y_test), axis=0)
for trait_name, mae_val in zip(big5_traits, trait_mae):
    print(f"{trait_name}: MAE={mae_val:.4f}, accuracy~={1.0 - mae_val:.4f}")


Test MAE (overall): 0.13274754583835602
Approx. accuracy (1 - MAE): 0.867252454161644
61/61 ━━━━━━━━━━━━━━━━━━━━ 3s 33ms/step
extraversion: MAE=0.1369, accuracy~=0.8631
neuroticism: MAE=0.1383, accuracy~=0.8617
agreeableness: MAE=0.1200, accuracy~=0.8800
conscientiousness: MAE=0.1364, accuracy~=0.8636
openness: MAE=0.1322, accuracy~=0.8678
